# Restructuring Data E-Commerce Customer Support Conversations

conversation column is back-and-forth between agent and customer

source: https://huggingface.co/datasets/NebulaByte/E-Commerce_Customer_Support_Conversations



In [5]:
import pandas as pd

In [6]:
df = pd.read_json('customer_agent.json', lines=True)
df.head()

issue_area                        issue_category  \
0          Login and Account  Mobile Number and Email Verification   
1  Cancellations and returns                   Pickup and Shipping   
2  Cancellations and returns        Replacement and Return Process   
3          Login and Account       Login Issues and Error Messages   
4                      Order                 Order Delivery Issues   

                                  issue_sub_category  \
0  Verification requirement for mobile number or ...   
1           Reasons for being asked to ship the item   
2             Inability to click the 'Cancel' button   
3  Error message regarding exceeded attempts to e...   
4                       Delivery not attempted again   

                         issue_category_sub_category customer_sentiment  \
0  Mobile Number and Email Verification -> Verifi...            neutral   
1  Pickup and Shipping -> Reasons for being asked...            neutral   
2  Replacement and Return Process -> Inability to...            neutral   
3  Login Issues and Error Messages -> Error messa...            neutral   
4  Order Delivery Issues -> Delivery not attempte...           negative   

  product_category       product_sub_category issue_complexity  \
0       Appliances  Oven Toaster Grills (OTG)           medium   
1      Electronics           Computer Monitor             less   
2       Appliances       Juicer/Mixer/Grinder           medium   
3       Appliances             Water Purifier             less   
4      Electronics                 Bp Monitor           medium   

  agent_experience_level                        agent_experience_level_desc  \
0                 junior  handles customer inquiries independently, poss...   
1                 junior  handles customer inquiries independently, poss...   
2            experienced  confidently handles complex customer issues, e...   
3          inexperienced  may struggle with ambiguous queries, rely on c...   
4            experienced  confidently handles complex customer issues, e...   

                                        conversation  
0  Agent: Thank you for calling BrownBox Customer...  
1  Agent: Thank you for calling BrownBox customer...  
2  Agent: Thank you for calling BrownBox Customer...  
3  Customer: Hi, I am facing an issue while loggi...  
4  Agent: Thank you for contacting BrownBox custo...

In [7]:
# ## this splits customer and agent lines into separate columns for every conversation
# ## conversations are not grouped... not the best rn

# # make pandas dataframe with 1 column (conversation)
# conversation = df['conversation']
# conversation.head()
# # print(conversation[1])

# agent_customer_df = pd.DataFrame(columns=['Agent', 'Customer'])

# for row in conversation:
#     convo = row.split('\n\n') # ['Agent: ...', 'Customer: ...']
#     agent_lines = []
#     customer_lines = []
#     for piece in convo:
#         parts = piece.split(': ', 1) # split into 'speaker' and 'lines'
#         if len(parts) == 2:  # check if the split was successful
#             speaker, line = parts
#             if speaker == 'Agent':
#                 agent_lines.append(line)
#             elif speaker == 'Customer':
#                 customer_lines.append(line)
#         else:
#             # no speaker: message format --> how do i deal with this??
#             print(f'skipping unexpected format: {piece}')
            
#             continue
    
#         if len(agent_lines) and len(customer_lines):
#             # print('agent_lines: ', agent_lines, 'customer_lines: ', customer_lines)
#             agent_text = agent_lines.pop()
#             customer_text = customer_lines.pop()
#             new_row_df = pd.DataFrame({'Agent': [agent_text], 'Customer': [customer_text]})
#             agent_customer_df = pd.concat([agent_customer_df, new_row_df], ignore_index=True)
#         else: 
#             continue

# agent_customer_df


    
        
        

In [8]:
# from json import loads, dumps

# # make pandas dataframe with 1 column (conversation)
# conversation = df['conversation']
# conversation.head()
# # print(conversation[1])

# agent_customer_df = pd.DataFrame(columns=['Agent', 'Customer'])
# with open('multiturn_chats.json', 'w') as file:
#     for row in conversation:
#         dictionary = {}
#         convo = row.split('\n\n') # ['Agent: ...', 'Customer: ...']
#         for piece in convo:
#             parts = piece.split(': ', 1) # split into 'speaker' and 'lines'
#             if len(parts) == 2:  # check if the split was successful
#                 speaker, line = parts
#                 if speaker == 'Agent':
#                     dictionary['Agent'] = line
#                 elif speaker == 'Customer':
#                     dictionary['Customer'] = line
#             else:
#                 # no speaker: message format --> how do i deal with this??
#                 # print(f'skipping unexpected format: {piece}')
#                 continue
#             if len(dictionary) == 2:
#                 json_string = dumps(dictionary['Agent'])
#                 file.write(json_string + '\n')
#                 json_string = dumps(dictionary['Customer'])
#                 file.write(json_string + '\n')
                
# # open the file for reading
# with open('multiturn_chats.json', 'r') as file:
#     for line in file:
#         # turn each line (json string) back into a python object
#         conversation = loads(line)
#         # conversation dictionary
#         print(conversation)


### Reformat Conversations

In [18]:
import json

def reformat_conversation(conversation):
    lines = conversation.split('\n\n')
    reformatted = []
    for line in lines:
        if line.startswith('Agent:'):
            reformatted.append({"role": "assistant", "content": line.replace('Agent: ', '')})
        elif line.startswith('Customer:'):
            reformatted.append({"role": "user", "content": line.replace('Customer: ', '')})
    return reformatted

def process_file_line_by_line(input_file_path, output_file_path):
    reformatted_data = []
    
    # process each line as separate json object
    with open(input_file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                item = json.loads(line)
                conversation = item.get('conversation', '')
                reformatted_conversation = reformat_conversation(conversation)
                
                system_message = {"role": "system", "content": "A polite chatbot that deals with e-commerce products."}
                reformatted_conversation.insert(0, system_message)
                reformatted_data.append({"messages": reformatted_conversation})
            except json.JSONDecodeError:
                print("Error decoding JSON from line:", line)
                continue
    
    # write reformatted conversations to new json file
    with open(output_file_path, 'w', encoding='utf-8') as outfile:
        json.dump(reformatted_data, outfile, ensure_ascii=False, indent=4)

# specify path to input file and desired output file
input_file_path = 'customer_agent.json'
output_file_path = 'converted_conversations.json'

# process file
process_file_line_by_line(input_file_path, output_file_path)

output_file_path

f = open(output_file_path)
data = json.load(f)
with open(output_file_path, 'r') as f:
    with open('converted_conversations.jsonl', 'w') as outfile:
        for entry in data:
            json.dump(entry, outfile)
            outfile.write('\n')
            
        


In [22]:
import os
from openai import OpenAI
from dotenv import load_dotenv
load_dotenv()

client = OpenAI()

conversations_path = 'converted_conversations.jsonl'

with open(conversations_path, "rb") as file:
    file_content = file.read()

# won't open file, looking for file object?
client.fine_tuning.jobs.create(
  file=open(file_content, "rb"),
  purpose="fine-tune"
)

OSError: [Errno 63] File name too long: b'{"messages": [{"role": "system", "content": "A polite chatbot that deals with e-commerce products."}, {"role": "assistant", "content": "Thank you for calling BrownBox Customer Support. My name is Tom. How may I assist you today?"}, {"role": "user", "content": "Hi Tom, I\'m trying to log in to my account to purchase an Oven Toaster Grill (OTG), but I\'m unable to proceed as it\'s asking for mobile number or email verification. Can you help me with that?"}, {"role": "assistant", "content": "Sure, I can assist you with that. May I know your registered mobile number or email address, please?"}, {"role": "user", "content": "My registered mobile number is +1 123-456-7890."}, {"role": "assistant", "content": "Thank you. Let me check that for you. I\'m sorry to inform you that we don\'t have this number on our records. Can you please confirm if this is the correct number?"}, {"role": "user", "content": "Oh, I\'m sorry. I might have registered with a di

In [ ]:
completion = client.chat.completions.create(
  model="gpt-3.5-turbo",
  messages=outfile

)

print(completion.choices[0].message)

BadRequestError: Error code: 400 - {'error': {'message': "'converted_conversations.json' is not of type 'array' - 'messages'", 'type': 'invalid_request_error', 'param': None, 'code': None}}

In [ ]:
completion = client.chat.completions.create(
  model="gpt-3.5-turbo",
  messages=[
            {
              "role": "system", "content": "A polite chatbot that deals with e-commerce products."
            },
            {
                "role": "assistant",
                "content": "Thank you for calling BrownBox Customer Support. My name is Tom. How may I assist you today?",
                
            },
            {
                "role": "user",
                "content": "Hi Tom, I'm trying to log in to my account to purchase an Oven Toaster Grill (OTG), but I'm unable to proceed as it's asking for mobile number or email verification. Can you help me with that?"
            },
            {
                "role": "assistant",
                "content": "Sure, I can assist you with that. May I know your registered mobile number or email address, please?",
              
            },
            {
                "role": "user",
                "content": "My registered mobile number is +1 123-456-7890."
            }
            ]

)

print(completion.choices[0].message)

ChatCompletionMessage(content='Thank you for providing your mobile number. Let me assist you in verifying your account. I will send a verification code to your mobile number. Please provide me with the code once you receive it.', role='assistant', function_call=None, tool_calls=None)
